# Additive synthesis tutorial

This method synthesizes sounds by constructing a complex tone made of a fundamental and several harmonics. The tone is obtained by adding together all these components.

In [ ]:
# Import modules

import math
import numpy as np
import matplotlib.pyplot as plt
import IPython.display as ipd
from scipy.signal import freqz
from scipy.signal import sosfreqz

<br>
The function below can be used to synthesize a complex tone containing a fundamental frequency and a number of its harmonics, all scaled by different amplitudes and added to one another at different phase shifts. The number of components is set to 5 currently, but can be easily changed by passing a value for the argument 'n_comp' when calling the function.
<br>

In [ ]:
# Function to generate complex tone

def generate_complex_tone(f0, fs, amplitudes, phases, duration, n_comp=5):
    '''
    Arguments:
    f0 - fundamental freq
    fs - sampling freq
    amplitudes, phases - absolute amplitude and phase value for the f0 and the harmonics
    
    Returns the complex tone signal
    '''
    assert len(amplitudes) == n_comp, "Incorrect number of amplitudes provided"
    assert len(phases) == n_comp, "Incorrect number of phases provided"
    
    n=np.arange(0,duration*fs)
    x=np.zeros(len(n))
    
    for i in range(len(amplitudes)):
        x = x + amplitudes[i]*np.sin(2*np.pi*(i+1)*(f0/fs)*n + phases[i])
    return x

<br>
Set the parameters for synthesis - the F0, duration, amplitudes and phases of all the components.

In [ ]:
# Parameters for synthesis

pi = np.pi
f0=500                   #in Hz
fs=16000                 #in samples/s
amplitudes=[1,1,1,1,1]
phases=[pi/2,pi/2,pi/2,pi/2,pi/2]
duration=1              #in seconds

<br>
Call the function to generate the tone and plot its waveform and magnitude spectrum. Play around with the values of the amplitudes & phases and see if you notice any changes in the resulting audio and plots. Also observe the effect of changing the fs, f0 and n_fft on the magnitude spectrum.

In [ ]:
# Change below line to '%matplotlib notebook'  to allow zooming in, moving the plot around, etc.
%matplotlib inline 

# Generate a tone based on above specifications
x = generate_complex_tone(f0,fs,amplitudes,phases,duration,n_comp=5)

# Calculate the DFT of x
n_fft=256
x_spec = np.fft.rfft(x,n_fft)

t = np.arange(len(x))/fs
f = np.arange(len(x_spec))*fs/(2*len(x_spec))

# Plot the waveform
fig,ax=plt.subplots(1,2,figsize=(15, 3))
ax[0].plot(t[:5*fs//f0], x[:5*fs//f0])
ax[0].set_title('Waveform'); ax[0].set_xlabel('Time (s)')
ax[0].minorticks_on(); ax[0].grid(which='both')

# Plot the magnitude spectrum
ax[1].plot(f, np.abs(x_spec))
ax[1].set_title('Magnitude Spectrum')
ax[1].set_xlabel('Frequency (Hz)'); ax[1].set_ylabel('Magnitude')
ax[1].minorticks_on(); ax[1].grid(which='both')

plt.show()
ipd.display(ipd.Audio(data=x, rate=fs))

<br><br>
## A simple example of generating a melody using the synthesis block from above

In this task, we will generate a melody by synthesizing the corresponding the notes and setting the durations of each note appropriately. You can use the chart below as a reference for the absolute F0 values of musical notes.

| Note | Freq (Hz)   | Note | Freq (Hz)   | Note | Freq (Hz)   |
|------|-------------|------|-------------|------|-------------|
|   C1 |     131     |   F  |     175     |   A# |     233     |
|   C# |     139     |   F# |     185     |   B  |     247     |
|   D  |     147     |   G  |     196     |   C2 |     262     |
|   D# |     156     |   G# |     208     |
|   E  |     165     |   A  |     220     |

Following is the note sequence(score) for a popular melody. Each tuple specifies (Note, #beats). Take 1 beat = 400 ms.  

(C,1) (C, 1) (D,2) (C,2) (F,2) (E,4);

(C,1) (C,1) (D,2) (C,2) (G,2) (F,4);

(C,1) (C,1) (C2,2) (A,2) (F,2) (E,2) (D,2);

(A#,1) (A#,1) (A,2) (F,2) (G,2) (F,4);

<br>
Convert the above note-freq. chart and score to a python dictionary and list, respectively

In [ ]:
note_freq = {'C':131, 'C#':139, 'D':147, 'D#':156, 
         'E':165, 'F':175, 'F#':185, 'G':196, 
         'G#':208, 'A':220, 'A#':233, 'B':247, 'C2':262}

melody = [('C',1), ('C', 1), ('D',2), ('C',2), ('F',2), ('E',4), 
          ('C',1), ('C',1), ('D',2), ('C',2), ('G',2), ('F',4), 
          ('C',1), ('C',1), ('C2',2), ('A',2), ('F',2), ('E',2), ('D',2),
          ('A#',1), ('A#',1), ('A',2), ('F',2), ('G',2), ('F',4)]


<br>
Then synthesize the melody using the method from above

In [ ]:
fs = 16000
beat_dur = 200e-3

synth_song = np.array([])
for note in melody:
    f0 = note_freq[note[0]]
    duration = note[1]*beat_dur
    
    # synthesize note using a complex tone
    x = generate_complex_tone(f0,fs,[1,1,1,1,1],[0,0,0,0,0],duration)
    
    # append to synth_song array:
    synth_song = np.append(synth_song, x)
    
ipd.display(ipd.Audio(data=synth_song, rate=fs))

<br><b>Acknowledgement</b>: This notebook was created by Rohit M A and Kamini Sabu, graduate students at DAP Lab, Dept of EE, IIT Bombay.<br>
Please contact Prof. Preeti Rao at prao@ee.iitb.ac.in in case of any queries.